In [1]:
from random import uniform
import numpy as np
import pandas as pd
from math import sqrt
import plotly.graph_objects as go
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)

In [2]:
import plotly
plotly.__version__


'5.3.1'

In [3]:
def plot_surface(func):
    x = np.linspace(0, 100, 100).reshape(1, -1)
    y = np.linspace(0, 100, 100).reshape(1, -1)
    f = np.array([[func(x_i, y_j) for y_j in y[0]] for x_i in x[0]])

    layout = go.Layout(scene=dict(aspectmode='cube'))


    fig = go.Figure(data=[go.Surface(z=f)], layout=layout, )

    legend=dict(font=dict(size=12), x=0.45, y=0.95,)

    fig.update_layout(autosize=True,
                      width=800, height=500,
                      margin=dict(l=0, r=50, b=100, t=0),
                      legend=legend,
                      )
    
    return fig

    
def plot_gradient_descent_steps(fig, x_steps, y_steps, func_steps):
    steps = go.Scatter3d(x=x_steps,
                             y=y_steps,
                             z=func_steps,
                             mode='lines+markers',
                             marker=dict(
                                        size=5,
                                        color='red',
                                        colorscale='Viridis',
                             ),
                            line=dict(
                                color='red',
                                width=2
                            )
                        )
    fig.add_trace(steps)
    fig.show()
    return steps
    

In [4]:
def func_1(x, y):
    # смещаем начало координат в точку (50, 50). чтобы поверхность отображалась в нужном месте
    x -= 50
    y -= 50
    
    return x ** 2 + y ** 2

plot_surface(func_1)

In [5]:
# в аргументах передаются:
#
#     f -- функция зависящая от двух переменных
#     x0, y0 -- точка, в которой требуется вычислить градиент
#
# опционально можно указать:
#     dx, dy -- дельты по направлениям

def gradient_finite_diff(f, x0, y0, dx=0.0001, dy=0.0001):
    # частная производная по направлению оси х
    df_dx = (f(x0+dx, y0)-f(x0,y0))/dx # < ВАШ КОД: замените 0 на нужное выражение > 
    
    # частная производная по направлению оси у
    df_dy = (f(x0, y0+dy)-f(x0,y0))/dy # < ВАШ КОД: замените 0 на нужное выражение > 
    
    return (df_dx, df_dy)

In [6]:
eps = 0.001

def grad_norm(grad):
    return (grad[0] ** 2 + grad[1] ** 2) ** (1/2)


# в аргументах передаются:
#
#     f -- функция зависящая от двух переменных
#
# опционально можно указать:
#
#     (x0, y0) -- точка, с которой будет стартовать градиентный спуск, по умолчанию выбирается случайная точка
#     learning_rate -- подробнее об этом в соответствующих уроках
#     max_steps_number -- максимальное число шагов градиентного спуска
#     plot -- рисовать ли график


def gradient_descent(f,
                     x0=uniform(0, 100),
                     y0=uniform(0, 100),
                     learning_rate=0.1,
                     rho=0.9,
                     ep=1e-3,
                     max_steps_number=10000,
                     plot=True):
    # рисуем поверхность
    if plot:
        fig = plot_surface(f)
    
    # cтартуем с (x0, y0)
    step_number = 0
    x = x0
    y = y0
    
    # сохраняем последовательность наших шагов
    steps_x = [x0]
    steps_y = [y0]
    steps_func = [f(x0, y0)]
    # list of the sum square gradients for each variable
    sq_grad_avg = [0.0 for _ in range(2)]
    # list of the average parameter updates
    sq_para_avg = [0.0 for _ in range(2)]
    # критерий остановки градиентного спуска:
    #        либо градиент становится близким к 0
    #        либо сделано максимальное число шагов
    while step_number < max_steps_number and grad_norm(gradient_finite_diff(f, x, y)) > eps:
        # вычисляем градиент (получаем вектор с двумя компонентами, он понадобится в шаге градиентного спуска)
        grad = gradient_finite_diff(f, x, y)
        for i in range(2):
            # calculate the squared gradient
            sg = grad[i]**2.0
            # update the moving average of the squared gradient
            sq_grad_avg[i] = (sq_grad_avg[i] * rho) + (sg * (1.0-rho))
        # шаг градиентного спуска
        change=grad[0]*(ep + sqrt(sq_para_avg[0])) / (ep + sqrt(sq_grad_avg[0]))
        x -= change # < ВАШ КОД: замените 0 на нужное выражение > 
        sq_para_avg[0] = (sq_para_avg[0] * rho) + (change**2.0 * (1.0-rho))
        
        change=grad[1]*(ep + sqrt(sq_para_avg[1])) / (ep + sqrt(sq_grad_avg[1]))
        y -= change # < ВАШ КОД: замените 0 на нужное выражение > 
        sq_para_avg[1] = (sq_para_avg[1] * rho) + (change**2.0 * (1.0-rho))

        # добавляем новую точку и значение в ней в список шагов
        steps_x.append(x)
        steps_y.append(y)
        steps_func.append(f(x, y))
        
        step_number += 1
    
    if plot:
        plot_gradient_descent_steps(fig, steps_x, steps_y, steps_func)
        
    if len(steps_x) == max_steps_number:
        print(f"gradient descent reached maximum number of steps, which is set to {max_steps_number}")
    else:
        print(f"gradient descent terminated after {(step_number + 1)} steps")

    print(f"terminal point of gradient descent is (%.10f, %.10f) with function value %.10f" % (steps_x[-1], steps_y[-1], steps_func[-1]))

## Эксперименты

Поэкспериментируйте с learning rate, начальной точкой.

Чтобы получить ответы на вопросы в шаге на Степике, используйте значние `max_steps_number` по умолчанию. Оно влияет на критерий остановки, поэтому с другими значниями ваши ответы могут не сойтись с нашими.

In [7]:
gradient_descent(func_1)

gradient descent terminated after 1479 steps
terminal point of gradient descent is (49.9999500006, 49.9995211218) with function value 0.0000002318


In [14]:
gradient_descent(func_1, ep=0.2)

gradient descent terminated after 111 steps
terminal point of gradient descent is (49.9999500000, 49.9994943899) with function value 0.0000002581


In [15]:
gradient_descent(func_1, ep=0.001)

gradient descent terminated after 1479 steps
terminal point of gradient descent is (49.9999500006, 49.9995211218) with function value 0.0000002318


In [16]:
gradient_descent(func_1, x0=0,y0=100,ep=0.1)

gradient descent terminated after 156 steps
terminal point of gradient descent is (49.9996307010, 50.0002693174) with function value 0.0000002089


In [17]:
gradient_descent(func_1, x0=0,y0=100,ep=0.99)

gradient descent terminated after 50 steps
terminal point of gradient descent is (49.9996442014, 50.0002558081) with function value 0.0000001920


In [18]:
gradient_descent(func_1, x0=0,y0=100, ep=0.999)

gradient descent terminated after 50 steps
terminal point of gradient descent is (49.9996820037, 50.0002180047) with function value 0.0000001486


In [19]:
gradient_descent(func_1, x0=0,y0=100, ep=1.)

gradient descent terminated after 50 steps
terminal point of gradient descent is (49.9996859106, 50.0002140977) with function value 0.0000001445
